In [1]:
import pandas as pd
import os
from datetime import datetime as dt

import itertools
import networkx as nx
import matplotlib.pyplot as plt

import plotly.graph_objects as go
from collections import Counter

import copy

base = os.getcwd() + "\\"

In [2]:
matches_raw =      pd.read_excel(base + "IPL_2024.xlsx", sheet_name = 'League Matches')
points_table_raw = pd.read_excel(base + "IPL_2024.xlsx", sheet_name = 'Points Table')
mapping      = pd.read_excel(base + "IPL_2024.xlsx", sheet_name = 'Mapping')

display(mapping)

Team Full Name     Team Half Name Team Abbr
0          Chennai Super Kings        Super Kings       CSK
1                 Punjab Kings              Kings      PBKS
2        Kolkata Knight Riders      Knight Riders       KKR
3             Rajasthan Royals             Royals        RR
4               Gujarat Titans             Titans        GT
5  Royal Challengers Bengaluru  Royal Challengers       RCB
6          Sunrisers Hyderabad          Sunrisers       SRH
7         Lucknow Super Giants       Super Giants       LSG
8               Delhi Capitals           Capitals        DC
9               Mumbai Indians            Indians        MI

In [3]:
matches = matches_raw.copy()
matches.columns = [i.replace("\n"," ") for i in matches.columns]
matches['DATETIME'] = pd.to_datetime(matches['DATE'] + " " + matches['TIME'])

matches = matches.merge(mapping[['Team Full Name','Team Abbr']].rename(columns = {'Team Full Name':'HOME', 'Team Abbr':'HOME_TEAM'}),on = 'HOME', how = 'left')
matches = matches.merge(mapping[['Team Full Name','Team Abbr']].rename(columns = {'Team Full Name':'AWAY', 'Team Abbr':'AWAY_TEAM'}),on = 'AWAY', how = 'left')

print(dt.now())
curr_date = dt(2024,5,5,19)
curr_date = dt.now()

future_matches = matches[matches['DATETIME']>curr_date]
display(future_matches)

2024-05-06 23:18:40.215161


MATCH NO  MATCH DAY       DATE  DAY    TIME                         HOME  \
55        56         47  07-May-24  Tue  7:30PM               Delhi Capitals   
56        57         48  08-May-24  Wed  7:30PM          Sunrisers Hyderabad   
57        58         49  09-May-24  Thu  7:30PM                 Punjab Kings   
58        59         50  10-May-24  Fri  7:30PM               Gujarat Titans   
59        60         51  11-May-24  Sat  7:30PM        Kolkata Knight Riders   
60        61         52  12-May-24  Sun  3:30PM          Chennai Super Kings   
61        62         52  12-May-24  Sun  7:30PM  Royal Challengers Bengaluru   
62        63         53  13-May-24  Mon  7:30PM               Gujarat Titans   
63        64         54  14-May-24  Tue  7:30PM               Delhi Capitals   
64        65         55  15-May-24  Wed  7:30PM             Rajasthan Royals   
65        66         56  16-May-24  Thu  7:30PM          Sunrisers Hyderabad   
66        67         57  17-May-24  Fri  7:30PM               Mumbai Indians   
67        68         58  18-May-24  Sat  7:30PM  Royal Challengers Bengaluru   
68        69         59  19-May-24  Sun  3:30PM          Sunrisers Hyderabad   
69        70         59  19-May-24  Sun  7:30PM             Rajasthan Royals   

                           AWAY      STADIUM            DATETIME HOME_TEAM  \
55             Rajasthan Royals        Delhi 2024-05-07 19:30:00        DC   
56         Lucknow Super Giants    Hyderabad 2024-05-08 19:30:00       SRH   
57  Royal Challengers Bengaluru  Dharamshala 2024-05-09 19:30:00      PBKS   
58          Chennai Super Kings    Ahmedabad 2024-05-10 19:30:00        GT   
59               Mumbai Indians      Kolkata 2024-05-11 19:30:00       KKR   
60             Rajasthan Royals      Chennai 2024-05-12 15:30:00       CSK   
61               Delhi Capitals    Bengaluru 2024-05-12 19:30:00       RCB   
62        Kolkata Knight Riders    Ahmedabad 2024-05-13 19:30:00        GT   
63         Lucknow Super Giants        Delhi 2024-05-14 19:30:00        DC   
64                 Punjab Kings     Guwahati 2024-05-15 19:30:00        RR   
65               Gujarat Titans    Hyderabad 2024-05-16 19:30:00       SRH   
66         Lucknow Super Giants       Mumbai 2024-05-17 19:30:00        MI   
67          Chennai Super Kings    Bengaluru 2024-05-18 19:30:00       RCB   
68                 Punjab Kings    Hyderabad 2024-05-19 15:30:00       SRH   
69        Kolkata Knight Riders     Guwahati 2024-05-19 19:30:00        RR   

   AWAY_TEAM  
55        RR  
56       LSG  
57       RCB  
58       CSK  
59        MI  
60        RR  
61        DC  
62       KKR  
63       LSG  
64      PBKS  
65        GT  
66       LSG  
67       CSK  
68      PBKS  
69       KKR

In [4]:
points_table = points_table_raw.copy()
points_table = points_table.merge(mapping[['Team Half Name','Team Abbr']].rename(columns = {'Team Half Name':'TEAM', 'Team Abbr':'TEAM_NAME'}),on = 'TEAM', how = 'left')
display(points_table)

TEAM  MATCHES  WON  LOST  PTS    NRR TEAM_NAME
0      Knight Riders       11    8     3   16  1.453       KKR
1             Royals       10    8     2   16  0.622        RR
2        Super Kings       11    6     5   12  0.700       CSK
3          Sunrisers       11    6     4   12  0.072       SRH
4       Super Giants       11    6     5   12 -0.371       LSG
5           Capitals       11    5     6   10 -0.442        DC
6  Royal Challengers       11    4     7    8 -0.049       RCB
7              Kings       11    4     7    8 -0.187      PBKS
8             Titans       11    4     7    8 -1.320        GT
9            Indians       12    3     8    8 -0.356        MI

In [5]:
class Team:
    def __init__(self, name, points=0):
        self.name = name
        self.points = points

class Match:
    def __init__(self, team1, team2):
        self.team1 = team1
        self.team2 = team2

team_pts = points_table[['TEAM_NAME','PTS']].set_index('TEAM_NAME').to_dict()['PTS']
teams = {t:Team(t,p) for t,p in team_pts.items()}

In [6]:
future_match_dict = future_matches.set_index('MATCH NO').T.to_dict()
match_dict = {k:Match(teams[v['HOME_TEAM']], teams[v['AWAY_TEAM']]) for k,v in future_match_dict.items()}

In [7]:
print(list([i.name for i in teams.values()]), list(match_dict.values()))


['KKR', 'RR', 'CSK', 'SRH', 'LSG', 'DC', 'RCB', 'PBKS', 'GT', 'MI'] [<__main__.Match object at 0x000001D707ED2AF0>, <__main__.Match object at 0x000001D707ED2D60>, <__main__.Match object at 0x000001D707894BE0>, <__main__.Match object at 0x000001D707894CA0>, <__main__.Match object at 0x000001D7078947F0>, <__main__.Match object at 0x000001D7078945B0>, <__main__.Match object at 0x000001D707894AC0>, <__main__.Match object at 0x000001D707894B50>, <__main__.Match object at 0x000001D707894790>, <__main__.Match object at 0x000001D707894970>, <__main__.Match object at 0x000001D707894F10>, <__main__.Match object at 0x000001D707894FA0>, <__main__.Match object at 0x000001D707894E80>, <__main__.Match object at 0x000001D707894A90>, <__main__.Match object at 0x000001D707894940>]


In [8]:
class MatchOutcome:
    def __init__(self, match, result, winners = [], parent=None):
        self.match = match
        self.result = result
        self.parent = parent
        self.children = []
        self.winners = winners
        # self.width = len(self.children)

        # if parent:
        #     self.width = result + 1
            
        #     self.level = self.parent.level + 1
        # else:
        #     self.level = 0
        #     self.width = result

        # print(self.level, self.width)

        # if match:
        #     print(f"{match.team1.name} v {match.team2.name} \t W - ",[match.team1.name,match.team2.name][result])
        #     if result==0: pt_tbl[match.team1.name]+=2
        #     else: pt_tbl[match.team2.name]+=2



        # print(sorted(tuple(pt_tbl.items()), key = lambda x: -x[1]))
        # self.pt_tbl = pt_tbl

def generate_match_tree(matches):
    root = MatchOutcome(None, None)
    generate_children(root, matches)
    return root

def generate_children(parent_node, remaining_matches):
    if not remaining_matches:
        return
    
    match = remaining_matches[0]
    for result in [0, 1]: 
        print(parent_node.winners)
        child_node = MatchOutcome(match, result,  parent_node.winners + [[match.team1.name,match.team2.name][result]], parent_node)
        parent_node.children.append(child_node)
        generate_children(child_node, remaining_matches[1:])



# print(points_dict)
root = generate_match_tree(list(match_dict.values()))
        

[]
['DC']
['DC', 'SRH']
['DC', 'SRH', 'PBKS']
['DC', 'SRH', 'PBKS', 'GT']
['DC', 'SRH', 'PBKS', 'GT', 'KKR']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR', 'SRH']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR', 'SRH', 'MI']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR', 'SRH', 'MI', 'RCB']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR', 'SRH', 'MI', 'RCB', 'SRH']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR', 'SRH', 'MI', 'RCB', 'SRH']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR', 'SRH', 'MI', 'RCB']
['DC', 'SRH', 'PBKS', 'GT', 'KKR', 'CSK', 'RCB', 'GT', 'DC', 'RR', 'SRH', 'MI', 'RCB', 'PBKS']
['DC',

In [9]:
def evaluate_condition(node, points_dict, check_team):
    # Example condition: Check if the leaf node's match result is a tie
    winning_pts = dict(Counter(node.winners))
    for t in points_dict.keys():
        if t not in winning_pts.keys():
            winning_pts[t] = 0
        else: winning_pts[t] = winning_pts[t]*2

            
    all_points = list({t: points_dict[t] + winning_pts[t] for t in points_dict.keys()}.items())
    
    all_points = sorted(list(all_points), key = lambda x: -x[-1])
    top4 = all_points[:3]

    if all([t in [i[0] for i in top4] for t in check_team]): 
        print(all_points)
        return True
    return False
    # return node.match is not None and node.match.team1.name == "Team A" and node.result == 1  # Replace with your condition

def prune_tree(root, points_dict, check_team):
    win_list = []
    stack = [root]
    leaf_node = []
    while stack:
        node = stack.pop()
        if not node.children:  # Leaf node
            leaf_node.append(node)
            if not evaluate_condition(node, dict(points_dict), check_team):
                # Prune subtree by removing all children
                node.parent.children.remove(node)
            else:
                win_list.append(node)
        else:
            stack.extend(node.children)
    return root, win_list, leaf_node

points_dict = points_table.set_index('TEAM_NAME').to_dict()['PTS']
pruned_tree, win_leaf, leaf_nodes = prune_tree(copy.deepcopy(root), points_dict, ["RCB"])

In [10]:
print(len(win_leaf)/len(leaf_nodes)*100)

0.0


In [11]:
def evaluate_condition(node, points_dict, check_team):
    # Example condition: Check if the leaf node's match result is a tie
    winning_pts = dict(Counter(node.winners))
    for t in points_dict.keys():
        if t not in winning_pts.keys():
            winning_pts[t] = 0
        else: winning_pts[t] = winning_pts[t]*2

            
    all_points = list({t: points_dict[t] + winning_pts[t] for t in points_dict.keys()}.items())
    
    all_points = [i[0] for i in sorted(list(all_points), key = lambda x: -x[-1])]

    return all_points.index(check_team)+1
    # top4 = all_points[:3]

    # if all([t in [i[0] for i in top4] for t in check_team]): 
    #     print(all_points)
    #     return True
    # return False

def prune_tree(root, points_dict, check_team):
    # print(check_team)
    point_list = []
    stack = [root]
    leaf_node = []
    while stack:
        node = stack.pop()
        if not node.children:  # Leaf node
            leaf_node.append(node)
            point_list.append(evaluate_condition(node, dict(points_dict), check_team))
            # if not evaluate_condition(node, dict(points_dict), check_team):
            #     # Prune subtree by removing all children
            #     node.parent.children.remove(node)
            # else:
            #     win_list.append(node)
        else:
            stack.extend(node.children)

    point_dict = dict(Counter(point_list))
    point_dict = {k:v/len(point_list) for k,v in point_dict.items()}
    return point_dict

points_dict = points_table.set_index('TEAM_NAME').to_dict()['PTS']

team_points = {}
for t in mapping['Team Abbr'].unique():
    print(t)
    team_points[t] =  prune_tree(copy.deepcopy(root), points_dict, t)

CSK
PBKS
KKR
RR
GT
RCB
SRH
LSG
DC
MI


In [12]:
team_points2 = {k:pd.DataFrame(v, index = [k]) for k,v in team_points.items()}
perc = pd.concat(team_points2.values()).T.sort_index().T.rename_axis('RANK')

perc = perc.fillna(0).applymap(lambda x: f'{x:.2%}').T

# Define a function to apply conditional formatting
def highlight_cells(val):
    return f'background-color: rgba(0, 100, 255, {val})'  # Green color with alpha based on value

# Apply styling to the DataFrame
styled_df = perc.style.applymap(highlight_cells)

# Render styled DataFrame
styled_df

In [13]:
def evaluate_condition(node, points_dict, check_team):
    # Example condition: Check if the leaf node's match result is a tie
    winning_pts = dict(Counter(node.winners))
    for t in points_dict.keys():
        if t not in winning_pts.keys():
            winning_pts[t] = 0
        else: winning_pts[t] = winning_pts[t]*2

            
    all_points = list({t: points_dict[t] + winning_pts[t] for t in points_dict.keys()}.items())
    
    all_points = [i[0] for i in sorted(list(all_points), key = lambda x: -x[-1])]

    return all_points.index(check_team)+1
    # top4 = all_points[:3]

    # if all([t in [i[0] for i in top4] for t in check_team]): 
    #     print(all_points)
    #     return True
    # return False

def prune_tree(root, points_dict, check_team):
    # print(check_team)
    point_list = []
    stack = [root]
    leaf_node = []
    leaf_scenes = []
    while stack:
        node = stack.pop()
        if not node.children:  # Leaf node
            leaf_node.append(node)
            rank = evaluate_condition(node, dict(points_dict), check_team)
            point_list.append(rank)

            leaf_scene = pd.DataFrame(data = list(node.winners)).T
            leaf_scenes.append(leaf_scene)
            # if not evaluate_condition(node, dict(points_dict), check_team):
            #     # Prune subtree by removing all children
            #     node.parent.children.remove(node)
            # else:
            #     win_list.append(node)
        else:
            stack.extend(node.children)

    point_dict = dict(Counter(point_list))
    point_dict = {k:v/len(point_list) for k,v in point_dict.items()}
    return leaf_scenes, point_list, point_dict

points_dict = points_table.set_index('TEAM_NAME').to_dict()['PTS']

team_points = {}
scenario = {}
# for t in mapping['Team Abbr'].unique():
for t in ['RCB']:
    print(t)
    leaf_scenes, point_list, point_dict = prune_tree(copy.deepcopy(root), points_dict, t)
    team_points[t] =  point_dict

    # scenario[t] = pd.DataFrame(columns = [f"{m.team1.name} v {m.team2.name}" for m in match_dict.values()])
    scenario[t] = pd.concat(leaf_scenes).reset_index(drop = True)
    scenario[t] = scenario[t].reset_index(drop=True).rename_axis('ID').reset_index().merge(pd.DataFrame(point_list).reset_index(drop=True).rename_axis('ID').reset_index(), on = 'ID', how = 'left')
    scenario[t].columns = ['ID'] + [f"{m.team1.name} v {m.team2.name}" for m in match_dict.values()] + ['RANK']

   

RCB


In [15]:
# display(scenario[t][scenario[t]['RANK']>4])

match_prob = {}
a = scenario[t][scenario[t]['RANK']<=4].copy()
for m in [f"{m.team1.name} v {m.team2.name}" for m in match_dict.values()]:
    v = a[m].value_counts(normalize = True).sort_values(ascending = True).rename_axis('MATCH').reset_index().T.reset_index()
    v.columns = v.iloc[0]
    v = v.iloc[1:,:]
    v = v.melt(id_vars = 'MATCH', var_name = 'WIN_TEAM', value_name = 'REQD_PERC').sort_values(by = 'REQD_PERC',ascending = False).iloc[:1,:]
    # .reset_index()
    match_prob[m] = v

final_scenario = pd.concat(match_prob.values()).reset_index(drop = True)


final_scenario['REQD_PERC'] = final_scenario['REQD_PERC'].fillna(0).apply(lambda x: f'{x:.2%}').T

# Define a function to apply conditional formatting
def highlight_cells(val):
    return f'background-color: rgba(0, 100, 255, {val})'  # Green color with alpha based on value

# Apply styling to the DataFrame
# final_scenario = final_scenario.style.apply(highlight_cells)

# Render styled DataFrame
final_scenario

MATCH WIN_TEAM REQD_PERC
0      DC v RR       RR    80.00%
1    SRH v LSG      LSG    60.00%
2   PBKS v RCB      RCB   100.00%
3     GT v CSK       GT   100.00%
4     KKR v MI       MI    50.00%
5     CSK v RR       RR   100.00%
6     RCB v DC      RCB   100.00%
7     GT v KKR      KKR    50.00%
8     DC v LSG       DC    60.00%
9    RR v PBKS     PBKS    50.00%
10    SRH v GT       GT    80.00%
11    MI v LSG       MI    70.00%
12   RCB v CSK      RCB   100.00%
13  SRH v PBKS     PBKS    80.00%
14    RR v KKR      KKR    50.00%

In [ ]:
def display_match_tree(fig, node, x, y, depth, spacing):
    # if node.prob<=0: 
    if node.match:
        fig.add_trace(go.Scatter(x=[x], y=[y], mode='text', text=[f"{node.match.team1.name} vs {node.match.team2.name}"], textposition="middle center"))
        fig.add_trace(go.Scatter(x=[x], y=[y - 0.1], mode='text', text=[f"Winner: {node.match.team1.name if node.result == 0 else node.match.team2.name}"], textposition="middle center"))
    if node.children:

    # print(node.width)
    # print(sorted(tuple(node.pt_tbl.items()), key = lambda x: -x[1]))
    # if node.width not in [0,None]:
        child_depth = depth + 1
        child_spacing = spacing / 2
        for i, child in enumerate(node.children):
            x0 = x + child_spacing * (2 * i - len(node.children) + 1)
            y0 = y - 1 - child_depth * 0.5
            fig.add_shape(type="line", x0=x, y0=y, x1=x0, y1=y0, line=dict(color="black", width=1))
            display_match_tree(fig, child, x0, y0, child_depth, child_spacing)


# Create Plotly figure
fig = go.Figure()

# Display the match tree
display_match_tree(fig, pruned_tree, 0, 0, 0, 1)

# Update layout
fig.update_layout(title="Interactive Match Tree", showlegend=False, xaxis=dict(visible=False), yaxis=dict(visible=False))

# Show plot
fig.show()

In [14]:
[f"{m.team1.name} v {m.team2.name}" for m in match_dict.values()] + ['POSITION']

['MI v SRH',
 'DC v RR',
 'SRH v LSG',
 'PBKS v RCB',
 'GT v CSK',
 'KKR v MI',
 'CSK v RR',
 'RCB v DC',
 'GT v KKR',
 'DC v LSG',
 'RR v PBKS',
 'SRH v GT',
 'MI v LSG',
 'RCB v CSK',
 'SRH v PBKS',
 'RR v KKR',
 'POSITION']

In [ ]:
[i.width for i in root.children]

In [ ]:
root.children[0].children[0].children[0].children[0].children[0].children[0].children[0].children[0].children[0].children[0].winners

In [ ]:
root.copy()
